In [11]:

import os
from xml.etree import ElementTree as ET
import optuna
import pandas as pd
import numpy as np
import seaborn as sns

In [12]:
# Function that replaces the c values in the feb file, given the material coefficient name and the dictionary
def replace_value(FILE:str, c: str, c_dict: dict, tag: str, routine: str):
    sub_dict = c_dict[c] # Call the Dictionary of the material tree that you want to modify its material coefficients
    material_id = [j for j in sub_dict][0] # Call the name (Key) of the material tree that you want to modify its material coefficient
    c_val = sub_dict[material_id] # Call the c (Value) of the material tree that you want to modify its material coeffecient

    # Instantiate the feb file
    tree = ET.parse(FILE)
    root = tree.getroot()
    
    if routine == 'Material':
        # find the material tree in the root
        contact_tree = root.findall('.//Material')
              # find the contact tree in the root
    elif routine == 'Friction':
        contact_tree = root.findall('.//Contact')
        
    # find the specific children tree that contains a name="" with the given name from the dictionary
    for child in contact_tree[0]:
        if child.attrib.get('name') == f'{material_id}':
            # find the c tree and modify its value
            for subchild in child:
                if subchild.tag == tag:
                    subchild.text = f'{c_val}' # set the new value here
                    break # exit the loop after modifying the value

    # write the modified tree to the file with the XML declaration
    tree.write(FILE, encoding="ISO-8859-1", xml_declaration=True)


def calculate_mean_displacement(file_name: str) -> float:
    displacement_values = []
    try:
        with open(file_name, 'r') as file:
            lines = file.readlines()

        for line in reversed(lines):
            if line.startswith('*Step'):
                # Found the start of the last step
                break
            else:
                parts = line.split(',')
                if len(parts) == 2:
                    try:
                        value = float(parts[1])
                        displacement_values.append(value)
                    except ValueError:
                        # Skip lines that don't have a valid float value
                        continue

        return sum(displacement_values) / len(displacement_values) if displacement_values else None
    except Exception as e:
         # Return None in case of any exception
        return None


# Optuna objective function that will suggest the friction coefficients value 
def objective_all(trial: optuna.trial.Trial) -> float:
    c1_value = trial.suggest_categorical('c1_value', range(4, 21)) #Previous opt: 1,25
    c4_value = trial.suggest_categorical('c4_value', range(4, 11)) #1,15
    c5_value = trial.suggest_categorical('c5_value', range(300, 1201)) #200,600


    mod_dictionary_mp = dict(c5_value={"Material1": c5_value}, 
              c4_value={"Material1": c4_value}, 
              c1_value={"Material1": c1_value})

    # Call the replace_value function to modify the friction coefficient value in the feb file
    for key in mod_dictionary_fc.keys():
    #for the friction coefficient, the tag is the full name (dictionary key)
        tag = key
        replace_value(key, mod_dictionary_fc, tag, 'Friction')

    for key in mod_dictionary_mp.keys():
        # Call the replace_values function to modify the material coefficients values in the feb file
        tag = key[:2]
        replace_value(FILE_30, key, mod_dictionary_mp, tag, 'Material')
        replace_value(FILE_60, key, mod_dictionary_mp, tag, 'Material')

    # Run the febio simulation
    os.system(f'febio3 -i {FILE_60}')

    # Calculate the mean displacement of the simulated feb file for the two subtendons
    gas_sim_mean = calculate_mean_displacement(f'{NAME}_GAS.txt')
    sol_sim_mean_60 = calculate_mean_displacement(f'{NAME_60}_SOL.txt')
    
    #Calculate the difference between the sol and gas simulated mean displacement, to determine the differential displacement
    diff_sim_sol_gas = float(abs(sol_sim_mean - gas_sim_mean))

    #Calculate the difference between the sol and gas experimental displacement, to determine the differential displacement
    diff_exp_sol_gas = float(abs(exp_disp_sol - exp_disp_gas))
    
     # Calculate the error between the simulated differential mean displacement and the experimental differential mean displacement for SOL and GAS
    disp_error = float(abs(diff_sim_sol_gas - diff_exp_sol_gas))
    
    #add another febio run, with 30%MVC
    os.system(f'febio3 -i {FILE_30}')
    
    #estimate the SOL displacement for 30%
    sol_sim_mean_30 = calculate_mean_displacement(f'{NAME_30}_SOL.txt')
    
    #Calculate the optimization function and return it 

    error_30 = ((sol_sim_mean_30 - exp_disp_sol_30)**2)/(exp_disp_sol_30)**2
    error_60 = ((sol_sim_mean_60 - exp_disp_sol_60)**2)/(exp_disp_sol_60)**2 
    
    error = error_30 + error_60
    
    #append all results to lists so they can be stored
    
    sol_sim_mean_60_all.append(sol_sim_mean_60)
    sol_sim_mean_30_all.append(sol_sim_mean_30)
    
    exp_disp_sol_60_all.append(exp_disp_sol_60)
    exp_disp_sol_30_all.append(exp_disp_sol_30)
    
    error_30_all.append(error_30)
    error_60_all.append(error_60)
    error_all.append(error)
    
    c5_all.append(c5_value)
    c4_all.append(c4_value)
    c1_all.append(c1_value)
    

    print(f'simulated 60% SOL displacement = {sol_sim_mean_60}\nsimulated 30% SOL displacement = {sol_sim_mean_30}\nelongation error = {error}')
    return error # Return the error

# Optuna objective function that will suggest the friction coefficients value 
def objective_fc(trial: optuna.trial.Trial) -> float:
    fric_coeff_sol_gas = trial.suggest_float('fric_coeff_sol_gas', 0.001, 0.999)


    # Modify your friction_dict to the new suggest friction coefficient
    # Lines for optimizing friction coefficient
    mod_dictionary = dict(fric_coeff={"SOL_GAS": fric_coeff_sol_gas})
    

    # Call the replace_value function to modify the friction coefficient value in the feb file
    for key in mod_dictionary.keys():
    #for the friction coefficient, the tag is the full name (dictionary key)
        tag = key
        replace_value(FILE, key, mod_dictionary, tag, 'Friction')

    # Run the febio simulation
    os.system(f'febio3 -i {FILE}')
    
    
# Calculate the mean displacement of the simulated feb file for the two subtendons
    sim_disp_sol = calculate_mean_displacement(f'{NAME}_SOL.txt')
    sim_disp_gas = calculate_mean_displacement(f'{NAME}_GAS.txt')

    
        #Calculate the simulated differential displacement
    sim_diff_disp = float(abs(sim_disp_sol - sim_disp_gas))

        #Calculate the experimental differential displacement
    exp_diff_disp = float(abs(exp_disp_sol - exp_disp_gas))
        
         # Calculate the error between the simulated differenrial displacement and the experimental differential displacement 
    diff_disp_error = float(abs(sim_diff_disp - exp_diff_disp))   
    
    #append all results to lists so they can be stored
    sim_diff_disp_all.append(sim_diff_disp)
    diff_disp_error_all.append(diff_disp_error)
    fc_sol_gas_all.append(fric_coeff_sol_gas)
    exp_diff_disp_all.append(exp_diff_disp)

    print(f'simulated diff displacement = {sim_diff_disp}\ndifferential displacement error = {diff_disp_error}')
    return diff_disp_error # Return the error

In [13]:
dir_master = r'D:...'
participants_dir = os.path.join(dir_master, 'participants')
results_dir = os.path.join(dir_master, 'results')
results_fc_dir = os.path.join(dir_master, 'results_fc')
input_parameters = pd.read_csv(os.path.join(participants_dir, 'optimization_displacement.csv'))
logger = []

In [14]:
input_parameters['SUBJECT'].values

array(['S01', 'S03', 'S04', 'S09', 'S12', 'S14', 'S17', 'S21', 'S24',
       'S27', 'S29', 'S31', 'S39'], dtype=object)

In [ ]:
#list all participants from the input csv file and take their subject number
participants = input_parameters['SUBJECT']


#loop through each participant 
for participant in participants:
    

    c5_all = []
    c4_all = []
    c1_all = []
    
    
    sol_sim_mean_60_all = []
    sol_sim_mean_30_all = []

    exp_disp_sol_60_all = []
    exp_disp_sol_30_all = []

    error_all = []
    error_30_all = []
    error_60_all = []

    fc_sol_gas_all = []
    diff_disp_error_all = []
    sim_diff_disp_all = []
    exp_diff_disp_all = []

    #try optimization, if there is an error move to next participant in batch
    try:
    
        p_name = participant
        dir_par = os.path.join(participants_dir, p_name)
        p_results_dir = os.path.join(results_dir, p_name)
        if not os.path.exists(p_results_dir):
            os.mkdir(p_results_dir)
        
        os.chdir(dir_par)
    
        results_all_path = os.path.join(p_results_dir, f'optimization_results_{p_name}_final.csv')
    
        if os.path.isfile(results_all_path):
            print('OPTMISATION ALREADY DONE')
            opt_results_all = pd.read_csv(results_all_path)
        else:
            NAME_60 = f'{participant}_W0_Type_I_60%MVC' # Name of the feb file without the .feb extension
            FILE_60 = f'{NAME_60}.feb'
            
            NAME_30 = f'{participant}_W0_Type_I_30%MVC' # Name of the feb file without the .feb extension
            FILE_30 = f'{NAME_30}.feb'
    
            # take the input displacement parameters from the optimization_diff_displacement_fc.csv file and change them for each participant
            p_params = input_parameters[input_parameters['SUBJECT'] == p_name]
        
            exp_disp_sol_60 = p_params['SOL_displacement_60'].iloc[0]
            exp_disp_sol_30 = p_params['SOL_displacement_30'].iloc[0]
            
            # start the friction coefficient optimization
            study_all = optuna.create_study(study_name=f'{participant}',
                                        storage=f'sqlite:///{os.getcwd()}/{participant}.db',
                                        directions=["minimize"], load_if_exists=True) 
            
            # Creates the study. The goal is to minimize the error, hence direction="minimize"
            study_all.optimize(objective_all, n_trials=800, n_jobs=1, gc_after_trial=True, show_progress_bar=True) # Runs the study, n_trials is the number of trials, n_jobs is the number of parallel jobs, gc_after_trial is whether to run garbage collection after each trial, show_progress_bar is whether to show the progress bar
            
            print("Number of finished trials: {}".format(len(study_all.trials))) # Verbose output for number of finish trials
            
            print("Number of finished trials: {}".format(len(study_all.trials))) # Verbose output for number of finish trials 
            opt_results_all = pd.DataFrame({'sim_sol_disp_60': sol_sim_mean_60_all, 'exp_disp_sol_60': exp_disp_sol_60_all, 
                                            'sim_sol_disp_30': sol_sim_mean_30_all, 'exp_disp_sol_30': exp_disp_sol_30_all,
                                           'c5_value': c5_all,'c4_value': c4_all,'c1_value': c1_all, 'error_60': error_60_all, 'error_30':error_30_all,'error': error_all})
            
            # output the friction coefficient optimization results as relative error
            opt_results_all['%_error'] = opt_results_all['error'] * 100
            opt_results_all = opt_results_all.sort_values('%_error', ascending = True)
            
            # create a new excel file with the final list of optimized friction coefficient
            opt_results_all.to_csv(results_all_path)
            
    
        #perform optimization of the friction coefficient, based on 60% MVC, and using the average material properties from the best sets of parameters with an error lower than 20%
        
        p_results_fc_dir = os.path.join(results_fc_dir, p_name)
        if not os.path.exists(p_results_fc_dir):
            os.mkdir(p_results_fc_dir)
        
        results_fc_path = os.path.join(p_results_fc_dir, f'optimization_results_{p_name}_fc.csv')
       
        best_run_all = opt_results_all[opt_results_all['%_error'] <= 20].mean()
                    
        NAME = f'{participant}_W0_Type_I_60%MVC_fc' # Name of the feb file without the .feb extension
        FILE = f'{NAME}.feb'
                
        
        mod_dictionary_mp = dict(c5_value={"Material1": best_run_all['c5_value']},
                                      #c4_value={"Material1": best_run_all['c4_value']},
                                     #c1_value={"Material1": best_run_all['c1_value']})
            
                
        for key in mod_dictionary_mp.keys():
                    # Call the replace_values function to modify the material coefficients values from the previou soptimization in the feb file
                tag = key[:2]
                replace_value(FILE, key, mod_dictionary_mp, tag, 'Material')
            
         # take the input displacement parameters from the input file and change them for each participant
        p_params = input_parameters[input_parameters['SUBJECT'] == p_name]
        exp_disp_sol = p_params['SOL_displacement_ST'].iloc[0]
        exp_disp_gas = p_params['GAS_displacement_ST'].iloc[0]
        
        # start the friction coefficient optimization
        study_fc = optuna.create_study(study_name=f'{NAME}',
                                    storage=f'sqlite:///{os.getcwd()}/{NAME}.db',
                                    directions=["minimize"], load_if_exists=True)
        
        # Creates the study. The goal is to minimize the error, hence direction="minimize"
        study_fc.optimize(objective_fc, n_trials=1000, n_jobs=1, gc_after_trial=True, show_progress_bar=True) # Runs the study, n_trials is the number of trials, n_jobs is the number of parallel jobs, gc_after_trial is whether to run garbage collection after each trial, show_progress_bar is whether to show the progress bar
        
        print("Number of finished trials: {}".format(len(study_all.trials))) # Verbose output for number of finish trials
            
        print("Number of finished trials: {}".format(len(study_all.trials))) # Verbose output for number of finish trials
    
        opt_results_fc = pd.DataFrame({'fc': fc_sol_gas_all, 'sim_diff_disp': sim_diff_disp_all,'error': diff_disp_error_all})
    
        # output the friction coefficient optimization results as relative error
        opt_results_fc['%_error'] = opt_results_fc['error'] / exp_diff_disp_all * 100
        opt_results_fc = opt_results_fc.sort_values('%_error', ascending = True)
        
        # create a new excel file with the final list of optimized friction coefficient
        opt_results_fc.to_csv(results_fc_path)

    except Exception as err:
        print(err)
        logger.append([participant, 'Optimization failed', err])

[I 2024-07-01 12:17:50,076] Using an existing study with name 'S04' instead of creating a new one.


OPTMISATION ALREADY DONE
OPTMISATION ALREADY DONE


Best trial: 1. Best value: 0.581457:   0%|          | 1/900 [01:34<23:42:49, 94.96s/it]

simulated 60% SOL displacement = 2.0482334472934465
simulated 30% SOL displacement = 1.3128458366571678
elongation error = 0.807192818143236
[I 2024-07-01 12:19:24,951] Trial 6 finished with value: 0.807192818143236 and parameters: {'c1_value': 9, 'c4_value': 5, 'c5_value': 958}. Best is trial 1 with value: 0.5814566640174665.


Best trial: 1. Best value: 0.581457:   0%|          | 2/900 [03:26<26:03:19, 104.45s/it]

...

simulated 60% SOL displacement = 1.6572917912205558
simulated 30% SOL displacement = 0.8589807837259101
elongation error = 0.9950538527873165
[I 2024-07-09 08:43:28,886] Trial 84 finished with value: 0.9950538527873165 and parameters: {'c1_value': 18, 'c4_value': 9, 'c5_value': 458}. Best is trial 52 with value: 0.20999434082746127.


Best trial: 52. Best value: 0.209994:  10%|▉         | 86/900 [1:56:11<19:35:30, 86.65s/it]

simulated 60% SOL displacement = 2.880937134903641
simulated 30% SOL displacement = 1.7026589432548174
elongation error = 0.4148340109108098
[I 2024-07-09 08:45:02,858] Trial 85 finished with value: 0.4148340109108098 and parameters: {'c1_value': 5, 'c4_value': 6, 'c5_value': 638}. Best is trial 52 with value: 0.20999434082746127.


Best trial: 52. Best value: 0.209994:  10%|▉         | 87/900 [1:57:19<18:18:47, 81.09s/it]

simulated 60% SOL displacement = 2.5976120074946434
simulated 30% SOL displacement = 1.4474802301927199
elongation error = 0.5446165607829325
[I 2024-07-09 08:46:10,984] Trial 86 finished with value: 0.5446165607829325 and parameters: {'c1_value': 9, 'c4_value': 4, 'c5_value': 409}. Best is trial 52 with value: 0.20999434082746127.
